In [1]:
# !pip install jsonlines
# # !pip install google_trans_new
# !pip install -U deep-translator
# !pip install langdetect

In [2]:
# from google.colab import drive
# drive.mount('/content/drive')

In [3]:
import numpy as np
import jsonlines as jsl
import pandas as pd
import json
from flatten_json import flatten
import re

# from google_trans_new import google_translator  
# from deep_translator import GoogleTranslator, single_detection
# from langdetect import detect

# TODO


- define list of filters (range/value)
- preprocess all strings into ints, floats


## Filter List
price, location(map), highlights.living area, highlights.plot size, number of bedrooms, number of rooms, price per m^2, parking, in_the_neighborhood, construction.type_of_house, location?, year_of_construction, ...

In [4]:

# trans = GoogleTranslator(source='nl', target='en', max_characters=20000)
# trans.translate("pindakaas")

# path = '/content/drive/MyDrive/ads.jsonlines'
path = '../Datasets/Funda/ads_trans.jsonlines'


In [5]:
reader = jsl.open(path)
first = reader.read()
first


{'crawl_time': 1685020679.2128732,
 'url': 'https://www.funda.nl/koop/amersfoort/huis-42126054-hogeweg-66/',
 'funda_identifier': '42126054',
 'images_paths': ['42126054/image3.jpeg',
  '42126054/image1.jpeg',
  '42126054/image4.jpeg',
  '42126054/image5.jpeg',
  '42126054/image2.jpeg'],
 'location_part1': 'Hogeweg 66',
 'location_part2': '3814 CE Amersfoort',
 'location_part3': 'Kruiskamp-Zuid',
 'price': '€ 450,000 k.k.',
 'highlights': {'living area': '110 m²',
  'plot size': '189 m²',
  'bedrooms': '2'},
 'features': {'transfer of ownership': {'asking price': '€ 450,000 kosten koper',
   'asking price per m²': "€ 4,091 The asking price per m² (€ 450,000) is calculated by dividing the asking price of the home by the living area (110 m²). Plot size and outbuildings aren't taken into account into this calculation. More information",
   'listed since': 'Today',
   'status': 'Available',
   'acceptance': 'Available in consultation'},
  'construction': {'kind of house': 'Single-family ho

In [6]:
data = []
file_path = path

# Read the .jsonlines file line by line
with open(file_path, 'r') as file:
    for line in file:
        try:       
            json_obj = json.loads(line)
        except:
            continue
        
        # Remove the 'images_paths' key and retrieve its value
        img_path = json_obj.pop('images_paths', '')
        neighb = json_obj.pop('in_the_neighborhood', '')
        
        json_obj = flatten(json_obj)
        json_obj['images_paths'] = img_path
        json_obj['in_the_neighborhood'] = neighb
        
        # Append the JSON object to the list
        data.append(json_obj)
        
        
# data[16000].keys()

In [7]:
df = pd.DataFrame.from_dict(data)
df.columns = df.columns.str.replace(' ', '_')

prefixes = ['features_', 'transfer_of_ownership_', 'construction_', 'surface_areas_and_volume_',
            'layout_', 'energy_', 'exterior_space_', 'storage_space_', 'parking_', 'geolocation_',
            'garage_', 'highlights_']

#remove prefixes created during flattening
for prefix in prefixes:
    df.columns = df.columns.str.replace(prefix, '')
    
#remove columns with duplicate names
df = df.loc[:, ~df.columns.duplicated()]

#remove irrelevant characteristics
df = df.filter(regex=r'^(?!vve_)')
df = df.drop(['asking_price','crawl_time', 'url', ], axis=1)


#remove properties without a set price
df['price'] = df['price'].str.replace(',', '').apply(lambda x: re.search(r'\d+', x).group(0) if re.search(r'\d+', x) else 'todrop')
df = df[df['price'] != 'todrop']
df['price'] = df['price'].astype(int)

#clean features with less than 1k non-empty values
df = df.dropna(axis=1, thresh=1000)
df = df.fillna('')

# df.head()


int_keys = [
    'living_area',
    'plot_size',
    'bedrooms',
    'year_of_construction',
    'volume_in_cubic_meters',
    'living_area',
    'external_storage_space',
#     'number_of_rooms',
#     'number_of_bath_rooms',
    'other_space_inside_the_building'

]

float_keys=[
    'asking_price_per_m²',
    'lat',
    'lon'
]

for key in float_keys:
    df[key] = df[key].str.replace(',', '.').apply(lambda x: float(re.findall(r'\d+\.\d+|\d+', x)[0]) if re.findall(r'\d+\.\d+|\d+', x) else 0.0).astype(float)

for key in int_keys:
    df[key] = df[key].apply(lambda x: x.replace(',', '') if isinstance(x, str) else str(x))
    df[key] = df[key].apply(lambda x: int(re.search(r'\d+', x).group(0)) if re.search(r'\d+', x) else 0).astype(int)



#TODO
#check if any more preprocessing is needed (check the example below and add the columns to the list of keys above)
#some keys (e.g. number of stories need to be checked for extra info other than number)
    

KeyError: 'plot_size'

In [ ]:
df

funda_identifier              location_part1       location_part2   
0            42126054                  Hogeweg 66   3814 CE Amersfoort  \
1            42126250                   Olivijn 8        5912 PV Venlo   
2            42189920                Dwarslaan 10     1261 BB Blaricum   
3            42115579           Vuurdoornstraat 1         6101 MB Echt   
4            42106112             Van Lennephof 1          5343 JC Oss   
...               ...                         ...                  ...   
8551         42127716        van Halewijnplein 18     2274 VC Voorburg   
8552         42102552  Petronella Brugsmastraat 2  3207 GR Spijkenisse   
8553         42102727        Middelburgseweg 1 A6  2741 LB Waddinxveen   
8554         42112028     Goeman Borgesiuslaan 15   1181 XZ Amstelveen   
8555         42114574       Loorijck (Bouwnr. 12)  7691 PV Bergentheim   

           location_part3    price  living_area  plot_size  bedrooms   
0          Kruiskamp-Zuid   450000          110        189         2  \
1              Hagerbroek   498000          160        333         4   
2           Blaricum-Dorp  1750000          206       1153         3   
3              Echt Noord   399000          157        419         4   
4         Vondellaan-Zuid   300000          124        205         4   
...                   ...      ...          ...        ...       ...   
8551  Voorburg Noord zuid   499500          128          0         4   
8552    Maaswijk-Zuidwest   675000          167        516         5   
8553                 Oost   395000           89          0         2   
8554         Elsrijk West   625000          109        168         4   
8555     Bergentheim Kern   392500          154        306         3   

      asking_price_per_m²  listed_since  ...   
0                   4.091         Today  ...  \
1                   3.112         Today  ...   
2                   8.495  May 12, 2023  ...   
3                   2.541  May 14, 2023  ...   
4                   2.419   May 8, 2023  ...   
...                   ...           ...  ...   
8551                3.902         Today  ...   
8552                4.042  May 12, 2023  ...   
8553                4.438  May 12, 2023  ...   
8554                5.734         Today  ...   
8555                2.549         Today  ...   

                                  type_of_roof   
0                                               \
1                                    Flat roof   
2           Gable roof covered with roof tiles   
3           Gable roof covered with roof tiles   
4           Gable roof covered with roof tiles   
...                                        ...   
8551                                             
8552  Pyramid hip roof covered with roof tiles   
8553                          Combination roof   
8554        Gable roof covered with roof tiles   
8555        Gable roof covered with roof tiles   

                                               location   
0                                                        \
1     Alongside a quiet road and in residential dist...   
2     Alongside a quiet road and In wooded surroundings   
3     Alongside a quiet road, In wooded surroundings...   
4                                                         
...                                                 ...   
8551  Alongside a quiet road, sheltered location and...   
8552  Alongside park, alongside water, sheltered loc...   
8553  Alongside a quiet road and unobstructed surrou...   
8554  Alongside a quiet road, in center and in resid...   
8555                            In residential district   

                               type_of_garage capacity   
0                                                       \
1                       Detached brick garage    1 car   
2     Parking place and detached brick garage   2 cars   
3                                    Built-in    1 car   
4                                    Built-in    1 car   
...             

In [ ]:
df.keys()

Index(['funda_identifier', 'location_part1', 'location_part2',
       'location_part3', 'price', 'living_area', 'bedrooms',
       'asking_price_per_m²', 'listed_since', 'status', 'acceptance',
       'building_type', 'year_of_construction', 'volume_in_cubic_meters',
       'number_of_rooms', 'number_of_bath_rooms', 'bathroom_facilities',
       'number_of_stories', 'facilities', 'label', 'insulation', 'heating',
       'hot_water', 'garden', 'type_of_facilities', 'lat', 'lon',
       'description', 'images_paths', 'in_the_neighborhood', 'type_of_roof',
       'location'],
      dtype='object')

28

In [31]:
df.iloc[0, df.columns.get_loc('images_paths')][0]

'42126054/image3.jpeg'

In [ ]:
df['lat']

0       52.15718
1       51.35439
2       52.27979
3       51.11259
4       51.74699
          ...   
1449    52.56520
1450    52.19217
1451    52.39311
1452    52.51184
1453    51.97467
Name: lat, Length: 1444, dtype: float64

In [ ]:
np.where(np.logical_and(df['lat']==52.15718,df['lon']==5.400165))

(array([0]),)

In [ ]:

np.mean((df['lon'], df['lat']), axis=1)

array([ 5.23481626, 52.10359635])

In [8]:
np.mean(df['lon'])

5.234816263850416

In [9]:
df['lon']

0       5.400165
1       6.172892
2       5.239072
3       5.875482
4       5.510582
          ...   
1449    4.994301
1450    5.370471
1451    4.642666
1452    4.949470
1453    6.728329
Name: lon, Length: 1444, dtype: float64

In [10]:
df.loc[5]


funda_identifier                                                   42118639
location_part1                                               Polderlaan 162
location_part2                                          2742 PP Waddinxveen
location_part3                                                     Triangel
price                                                                735000
living_area                                                             168
bedrooms                                                                  4
asking_price_per_m²                                                   4.375
listed_since                                                   May 17, 2023
status                                                            Available
acceptance                                        Available in consultation
building_type                                               Resale property
year_of_construction                                                   2022
volume_in_cu

In [11]:
import ini

In [12]:

from utils.file_utils import save_as_pickle

In [21]:
save_as_pickle('data.pkl', df)

In [14]:
from shapely.geometry import Point
from shapely.geometry.polygon import Polygon

In [15]:
df[['lat','lon']]

lat       lon
0     52.15718  5.400165
1     51.35439  6.172892
2     52.27979  5.239072
3     51.11259  5.875482
4     51.74699  5.510582
...        ...       ...
1449  52.56520  4.994301
1450  52.19217  5.370471
1451  52.39311  4.642666
1452  52.51184  4.949470
1453  51.97467  6.728329

[1444 rows x 2 columns]

In [16]:
df['coords'] = [Point(arr_el) for arr_el in df[['lat','lon']].to_numpy()]

In [17]:
df['coords']

0       POINT (52.15718 5.400165)
1       POINT (51.35439 6.172892)
2       POINT (52.27979 5.239072)
3       POINT (51.11259 5.875482)
4       POINT (51.74699 5.510582)
                  ...            
1449     POINT (52.5652 4.994301)
1450    POINT (52.19217 5.370471)
1451    POINT (52.39311 4.642666)
1452     POINT (52.51184 4.94947)
1453    POINT (51.97467 6.728329)
Name: coords, Length: 1444, dtype: object

In [18]:
array = df[['lat','lon']].to_numpy()
polygon = Polygon(np.array(array[:4]))
idces = np.where(polygon.contains([Point(arr_el) for arr_el in array]))[0]
df.iloc[idces]
# list(df.iloc[idces][['funda_identifier']])
df.iloc[idces][['funda_identifier']].to_numpy()

array([['42129744'],
       ['42129847'],
       ['42111646'],
       ['42129635'],
       ['42106314'],
       ['42110251'],
       ['42126943'],
       ['42113979'],
       ['42129978'],
       ['42108795'],
       ['42126728'],
       ['42118270'],
       ['42129046'],
       ['42129943'],
       ['42112313'],
       ['42127431'],
       ['42109989'],
       ['42182032'],
       ['42129077'],
       ['42104584'],
       ['42117632'],
       ['42113948'],
       ['42103731'],
       ['42100975'],
       ['42106682'],
       ['42125494']], dtype=object)

In [19]:
for row_dict in df.to_dict(orient="records"):
    print(row_dict)

{'funda_identifier': '42126054', 'location_part1': 'Hogeweg 66', 'location_part2': '3814 CE Amersfoort', 'location_part3': 'Kruiskamp-Zuid', 'price': 450000, 'living_area': 110, 'bedrooms': '2', 'asking_price_per_m²': 4.091, 'listed_since': 'Today', 'status': 'Available', 'acceptance': 'Available in consultation', 'building_type': 'Resale property', 'year_of_construction': '1905', 'volume_in_cubic_meters': '285 m³', 'number_of_rooms': '3 rooms (2 bedrooms)', 'number_of_bath_rooms': '1 bathroom and 2 separate toilets', 'bathroom_facilities': 'Bath and shower', 'number_of_stories': '2 stories and a loft', 'facilities': 'Optical fibre and flue', 'label': 'C', 'insulation': 'Roof insulation, double glazing and floor insulation', 'heating': 'CH boiler and wood heater', 'hot_water': 'CH boiler', 'garden': 'Back garden and front garden', 'type_of_facilities': 'Public parking', 'lat': 52.15718, 'lon': 5.400165, 'description': 'This charming and well-maintained single-family home is located clo

In [20]:
polygon_coords = [[5.370255, 52.141495], [5.370255, 52.18951], [5.443039, 52.18951], [5.443039, 52.141495], [5.370255, 52.141495]]
point = [52.15718, 5.400165]
